-sandbox
# Data Cleansing + Linear Regression with Airbnb

I will be using the SF Airbnb rental dataset from [Inside Airbnb](http://insideairbnb.com/get-the-data.html).

 - Impute missing values
 - Identify & substitute NaN values to the median of the column
 - Encode categorical features
 - Make a Linear regression Model
 - Calculate RMSE,MSE,MAE

In [0]:
%run "/Classroom-Setup"

Initialized classroom variables & functions...

Datasets are already mounted to /mnt/training from s3a://databricks-corp-training/common

In [0]:
%fs ls "dbfs:/mnt/training/airbnb/sf-listings/sf-listings-2019-03-06.csv"

path name size dbfs:/mnt/training/airbnb/sf-listings/sf-listings-2019-03-06.csv sf-listings-2019-03-06.csv 34234636

Read the csv to see some lines

In [0]:
%fs head "dbfs:/mnt/training/airbnb/sf-listings/sf-listings-2019-03-06.csv"

[Truncated to first 65536 bytes]
id,listing_url,scrape_id,last_scraped,name,summary,space,description,experiences_offered,neighborhood_overview,notes,transit,access,interaction,house_rules,thumbnail_url,medium_url,picture_url,xl_picture_url,host_id,host_url,host_name,host_since,host_location,host_about,host_response_time,host_response_rate,host_acceptance_rate,host_is_superhost,host_thumbnail_url,host_picture_url,host_neighbourhood,host_listings_count,host_total_listings_count,host_verifications,host_has_profile_pic,host_identity_verified,street,neighbourhood,neighbourhood_cleansed,neighbourhood_group_cleansed,city,state,zipcode,market,smart_location,country_code,country,latitude,longitude,is_location_exact,property_type,room_type,accommodates,bathrooms,bedrooms,beds,bed_type,amenities,square_feet,price,weekly_price,monthly_price,security_deposit,cleaning_fee,guests_included,extra_people,minimum_nights,maximum_nights,minimum_minimum_nights,maximum_minimum_nights,minimum_maximum_nights,maximum_maximum_nights,minimum_nights_avg_ntm,maximum_nights_avg_ntm,calendar_updated,has_availability,availability_30,availability_60,availability_90,availability_365,calendar_last_scraped,number_of_reviews,number_of_reviews_ltm,first_review,last_review,review_scores_rating,review_scores_accuracy,review_scores_cleanliness,review_scores_checkin,review_scores_communication,review_scores_location,review_scores_value,requires_license,license,jurisdiction_names,instant_bookable,is_business_travel_ready,cancellation_policy,require_guest_profile_picture,require_guest_phone_verification,calculated_host_listings_count,calculated_host_listings_count_entire_homes,calculated_host_listings_count_private_rooms,calculated_host_listings_count_shared_rooms,reviews_per_month
958,https://www.airbnb.com/rooms/958,20190306152813,2019-03-06,"Bright, Modern Garden Unit - 1BR/1B",New update: the house next door is under construction and there is the possibility of noise from 7am - 5pm. Our rates are discounted during this time period. Our bright garden unit overlooks a grassy backyard area with fruit trees and native plants. It is an oasis in a big city. The apartment comfortably fits a couple or small family. It is located on a cul de sac street that ends at lovely Duboce Park.,"Newly remodeled, modern, and bright garden unit in historic Victorian home. *New fixtures and finishes. *Organic cotton sheets and towels. *Zero VOC and non-toxic Yolo paint. *Organic and fair-trade teas, fresh local ground coffee. *Local art on walls. *Sofa bed and Queen bed are in the same room. More of a petite apartment with a separate room for dining and kitchen.","New update: the house next door is under construction and there is the possibility of noise from 7am - 5pm. Our rates are discounted during this time period. Our bright garden unit overlooks a grassy backyard area with fruit trees and native plants. It is an oasis in a big city. The apartment comfortably fits a couple or small family. It is located on a cul de sac street that ends at lovely Duboce Park. Newly remodeled, modern, and bright garden unit in historic Victorian home. *New fixtures and finishes. *Organic cotton sheets and towels. *Zero VOC and non-toxic Yolo paint. *Organic and fair-trade teas, fresh local ground coffee. *Local art on walls. *Sofa bed and Queen bed are in the same room. More of a petite apartment with a separate room for dining and kitchen. *Full access to patio and backyard (shared with us and our dog who live upstairs) *Beautiful garden with fruit trees, native plants and lawn *Washer and dryer *Children's toys *Charcoal grill A family of 4 lives upstairs ",none,"*Quiet cul de sac in friendly neighborhood *Steps away from grassy park with 2 playgrounds and Recreational Center *Very family-friendly neighborhood *Quaint shops, grocery stores and restaurants all within a 5-10 minute walk","Due to the fact that we have children and a dog, we are up early 7-8am and their footsteps or paws can be heard fr

Declared various utility methods: 
 Declared untilStreamIsReady( name:String ) to control workflow 
 
 All done!

Load the Airbnb dataset in.

In [0]:
import pandas as pd
filePath = "dbfs:/mnt/training/airbnb/sf-listings/sf-listings-2019-03-06.csv"

rawDF = spark.read.csv(filePath, header="true", inferSchema="true", multiLine="true", escape='"')


display(rawDF)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 958 https://www.airbnb.com/rooms/958 20190306152813 2019-03-06 Bright, Modern Garden Unit - 1BR/1B New update: the house next door is under construction and there is the possibility of noise from 7am - 5pm. Our rates are discounted during this time period. Our bright garden unit overlooks a grassy backyard area with fruit trees and native plants. It is an oasis in a big city. The apartment comfortably fits a couple or small family. It is located on a cul de sac street that ends at lovely Duboce Park. Newly remodeled, modern, and bright garden unit in historic Victorian home. *New fixtures and finishes. *Organic cotton sheets and towels. *Zero VOC and non-toxic Yolo paint. *Organic and fair-trade teas, fresh local ground coffee. *Local art on walls. *Sofa bed and Queen bed are in the same room. More of a petite apartment with a separate room for dining and kitchen. New update: the house next door is under construction and there is the possibility of noise from 7am - 5pm. Our rates are discounted during this time period. Our bright garden unit overlooks a grassy backyard area with fruit trees and native plants. It is an oasis in a big city. The apartment comfortably fits a couple or small family. It is located on a cul de sac street that ends at lovely Duboce Park. Newly remodeled, modern, and bright garden unit in historic Victorian home. *New fixtures and finishes. *Organic cotton sheets and towels. *Zero VOC and non-toxic Yolo paint. *Organic and fair-trade teas, fresh local ground coffee. *Local art on walls. *Sofa bed and Queen bed are in the same room. More of a petite apartment with a separate room for dining and kitchen. *Full access to patio and backyard (shared with us and our dog who live upstairs) *Beautiful garden with fruit trees, native plants and lawn *Washer and dryer *Children's toys *Charcoal grill A family of 4 lives upstairs none *Quiet cul de sac in friendly neighborhood *Steps away from grassy park with 2 playgrounds and Recreational Center *Very family-friendly neighborhood *Quaint shops, grocery stores and restaurants all within a 5-10 minute walk Due to the fact that we have children and a dog, we are up early 7-8am and their footsteps or paws can be heard from the apartment. Our place is ideal for ea

For the sake of simplicity, only keep certain columns from this dataset.

In [0]:
columnsToKeep = [
  "host_is_superhost",
  "cancellation_policy",
  "instant_bookable",
  "host_total_listings_count",
  "neighbourhood_cleansed",
  "latitude",
  "longitude",
  "property_type",
  "room_type",
  "accommodates",
  "bathrooms",
  "bedrooms",
  "beds",
  "bed_type",
  "minimum_nights",
  "number_of_reviews",
  "review_scores_rating",
  "review_scores_accuracy",
  "review_scores_cleanliness",
  "review_scores_checkin",
  "review_scores_communication",
  "review_scores_location",
  "review_scores_value",
  "price"]

baseDF = rawDF.toPandas()[columnsToKeep]

In [0]:
baseDF

host_is_superhost 
 cancellation_policy 
 instant_bookable 
 host_total_listings_count 
 neighbourhood_cleansed 
 latitude 
 longitude 
 property_type 
 room_type 
 accommodates 
 ... 
 minimum_nights 
 number_of_reviews 
 review_scores_rating 
 review_scores_accuracy 
 review_scores_cleanliness 
 review_scores_checkin 
 review_scores_communication 
 review_scores_location 
 review_scores_value 
 price 
 
 
 
 
 0 
 t 
 moderate 
 t 
 1 
 Western Addition 
 37.76931 
 -122.43386 
 Apartment 
 Entire home/apt 
 3 
 ... 
 1 
 180 
 97.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 $170.00 
 
 
 1 
 f 
 strict_14_with_grace_period 
 f 
 2 
 Bernal Heights 
 37.74511 
 -122.42102 
 Apartment 
 Entire home/apt 
 5 
 ... 
 30 
 111 
 98.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 9.0 
 $235.00 
 
 
 2 
 f 
 strict_14_with_grace_period 
 f 
 10 
 Haight Ashbury 
 37.76669 
 -122.45250 
 Apartment 
 Private room 
 2 
 ... 
 32 
 17 
 85.0 
 8.0 
 8.0 
 9.0 
 9.0 
 9.0 
 8.0 
 $65.00 
 
 
 3 
 f 
 strict_14_with_grace_period 
 f 
 10 
 Haight Ashbury 
 37.76487 
 -122.45183 
 Apartment 
 Private room 
 2 
 ... 
 32 
 8 
 93.0 
 9.0 
 9.0 
 10.0 
 10.0 
 9.0 
 9.0 
 $65.00 
 
 
 4 
 f 
 strict_14_with_grace_period 
 f 
 2 
 Western Addition 
 37.77525 
 -122.43637 
 House 
 Entire home/apt 
 5 
 ... 
 7 
 27 
 97.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 9.0 
 $785.00 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 7146 
 f 
 flexible 
 t 
 18 
 Noe Valley 
 37.74884 
 -122.42830 
 House 
 Entire home/apt 
 3 
 ... 
 30 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 $163.00 
 
 
 7147 
 t 
 flexible 
 t 
 10 
 Russian Hill 
 37.80645 
 -122.42109 
 Guest suite 
 Entire home/apt 
 2 
 ... 
 1 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 $160.00 
 
 
 7148 
 t 
 flexible 
 t 
 10 
 Western Addition 
 37.78855 
 -122.43110 
 Apartment 
 Entire home/apt 
 4 
 ... 
 2 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 $249.00 
 
 
 7149 
 f 
 flexible 
 t 
 87 
 Downtown/Civic Center 
 37.78645 
 -122.41458 
 Apartment 
 Entire home/apt 
 3 
 ... 
 30 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 $105.00 
 
 
 7150 
 f 
 flexible 
 f 
 87 
 Downtown/Civic Center 
 37.78645 
 -122.41458 
 Apartment 
 Entire home/apt 
 5 
 ... 
 30 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 $125.00 
 
 
 
 7151 rows × 24 columns

### Fixing Data Types

Change the type of the price column which has the substring ',' & '$'

In [0]:
fixedPriceDF=baseDF.copy()
#substitute the substring "$" and "," to "" using 'regex=True'
fixedPriceDF['price']=fixedPriceDF['price'].str.replace('$','',regex=True).str.replace(',','',regex=True).astype('float64')
display(fixedPriceDF)

host_is_superhost cancellation_policy instant_bookable host_total_listings_count neighbourhood_cleansed latitude longitude property_type room_type accommodates bathrooms bedrooms beds bed_type minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price t moderate t 1 Western Addition 37.76931 -122.43386 Apartment Entire home/apt 3 1.0 1.0 2.0 Real Bed 1 180 97.0 10.0 10.0 10.0 10.0 10.0 10.0 170.0 f strict_14_with_grace_period f 2 Bernal Heights 37.74511 -122.42102 Apartment Entire home/apt 5 1.0 2.0 3.0 Real Bed 30 111 98.0 10.0 10.0 10.0 10.0 10.0 9.0 235.0 f strict_14_with_grace_period f 10 Haight Ashbury 37.76669 -122.4525 Apartment Private room 2 4.0 1.0 1.0 Real Bed 32 17 85.0 8.0 8.0 9.0 9.0 9.0 8.0 65.0 f strict_14_with_grace_period f 10 Haight Ashbury 37.76487 -122.45183 Apartment Private room 2 4.0 1.0 1.0 Real Bed 32 8 93.0 9.0 9.0 10.0 10.0 9.0 9.0 65.0 f strict_14_with_grace_period f 2 Western Addition 37.77525 -122.43637 House Entire home/apt 5 1.5 2.0 2.0 Real Bed 7 27 97.0 10.0 10.0 10.0 10.0 10.0 9.0 785.0 f moderate f 1 Western Addition 37.78471 -122.44555 Apartment Entire home/apt 6 1.0 2.0 3.0 Real Bed 2 31 90.0 9.0 8.0 10.0 10.0 9.0 9.0 255.0 t strict_14_with_grace_period t 2 Mission 37.75919 -122.42237 Condominium Private room 3 1.0 1.0 2.0 Real Bed 1 647 98.0 10.0 10.0 10.0 10.0 10.0 10.0 139.0 f strict_14_with_grace_period f 1 Potrero Hill 37.76259 -122.40543 House Private room 2 1.0 1.0 1.0 Real Bed 1 453 94.0 10.0 10.0 10.0 10.0 10.0 10.0 135.0 t moderate f 1 Mission 37.75874 -122.41327 Apartment Entire home/apt 6 1.0 2.0 3.0 Real Bed 3 320 96.0 10.0 10.0 10.0 10.0 10.0 9.0 265.0 f strict_14_with_grace_period f 44 Haight Ashbury 37.77187 -122.43859 Apartment Entire home/apt 3 1.0 3.0 3.0 Real Bed 30 37 89.0 9.0 9.0 10.0 9.0 9.0 9.0 177.0 f strict_14_with_grace_period f 44 Western Addition 37.77355 -122.42436 Apartment Entire home/apt 5 2.0 3.0 3.0 Real Bed 30 14 91.0 10.0 10.0 10.0 9.0 10.0 9.0 194.0 f strict_14_with_grace_period f 44 Downtown/Civic Center 37.78574 -122.40798 Apartment Entire home/apt 2 1.5 1.0 1.0 Real Bed 30 19 92.0 10.0 9.0 10.0 10.0 10.0 9.0 139.0 f strict_14_with_grace_period f 10 Haight Ashbury 37.77019 -122.44594 Apartment Private room 2 4.0 1.0 2.0 Real Bed 32 6 80.0 9.0 8.0 9.0 10.0 9.0 7.0 85.0 f strict_14_with_grace_period f 10 Haight Ashbury 37.76894 -122.44778 Apartment Private room 2 3.0 1.0 2.0 Real Bed 32 5 64.0 6.0 6.0 10.0 9.0 9.0 8.0 85.0 t strict_14_with_grace_period t 1 Castro/Upper Market 37.76075 -122.43032 Apartment Private room 1 1.0 1.0 1.0 Real Bed 3 390 98.0 10.0 10.0 10.0 10.0 10.0 10.0 79.0 t strict_14_with_grace_period f 2 Inner Sunset 37.76203 -122.45455 Townhouse Entire home/apt 3 1.0 2.0 3.0 Real Bed 30 16 95.0 9.0 9.0 9.0 9.0 9.0 9.0 136.0 f moderate f 1 Mission 37.75491 -122.42246 Apartment Entire home/apt 3 1.0 1.0 2.0 Real Bed 3 103 97.0 10.0 9.0 10.0 10.0 10.0 10.0 215.0 f strict_14_with_grace_period f 3 South of Market 37.78647 -122.39072 Condominium Entire home/apt 4 2.0 2.0 2.0 Real Bed 90 14 96.0 10.0 10.0 10.0 10.0 10.0 9.0 450.0 t strict_14_with_grace_period f 1 Noe Valley 37.74888 -122.42982 Apartment Entire home/apt 3 1.0 0.0 1.0 Real Bed 30 61 96.0 10.0 10.0 10.0 10.0 10.0 10.0 107.0 t strict_14_with_grace_period f 3 Western Addition 37.77252 -122.43216 Townhouse Private room 2 1.0 1.0 1.0 Real Bed 2 363 97.0 10.0 10.0 10.0 10.0 10.0 10.0 110.0 t moderate f 1 Mission 37.76349 -122.41517 Guest suite Entire home/apt 2 1.0 0.0 1.0 Real Bed 5 227 96.0 10.0 10.0 10.0 10.0 9.0 9.0 198.0 t moderate f 1 Nob Hill 37.7958 -122.41533 Loft Entire home/apt 2 1.0 1.0 1.0 Real Bed 30 119 98.0 10.0 10.0 10.0 10.0 10.0 10.0 125.0 f strict_14_with_grace_period f 10 Haight Ashbury 37.7648 -122.45251 Apartment Private room 2 4.0 1.0 1.0 Real Bed 32 14 78.0 8.0 8.0 10.0 10.0 10.0 7.0 65.0 t strict_14_with_grace_period 

### Summary statistics

In [0]:
fixedPriceDF.describe(include='all')

host_is_superhost 
 cancellation_policy 
 instant_bookable 
 host_total_listings_count 
 neighbourhood_cleansed 
 latitude 
 longitude 
 property_type 
 room_type 
 accommodates 
 ... 
 minimum_nights 
 number_of_reviews 
 review_scores_rating 
 review_scores_accuracy 
 review_scores_cleanliness 
 review_scores_checkin 
 review_scores_communication 
 review_scores_location 
 review_scores_value 
 price 
 
 
 
 
 count 
 7151 
 7151 
 7151 
 7151.000000 
 7151 
 7151.000000 
 7151.000000 
 7151 
 7151 
 7151.000000 
 ... 
 7.151000e+03 
 7151.000000 
 5730.000000 
 5726.000000 
 5727.000000 
 5724.000000 
 5728.000000 
 5724.000000 
 5723.000000 
 7151.000000 
 
 
 unique 
 2 
 6 
 2 
 NaN 
 36 
 NaN 
 NaN 
 26 
 3 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 
 
 top 
 f 
 strict_14_with_grace_period 
 f 
 NaN 
 Mission 
 NaN 
 NaN 
 Apartment 
 Entire home/apt 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 
 
 freq 
 4219 
 3088 
 4434 
 NaN 
 692 
 NaN 
 NaN 
 3013 
 4366 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 
 
 mean 
 NaN 
 NaN 
 NaN 
 52.569571 
 NaN 
 37.765809 
 -122.430526 
 NaN 
 NaN 
 3.200951 
 ... 
 1.400030e+04 
 43.529157 
 95.546946 
 9.775585 
 9.624935 
 9.870021 
 9.841306 
 9.649371 
 9.405731 
 213.654034 
 
 
 std 
 NaN 
 NaN 
 NaN 
 177.371652 
 NaN 
 0.022527 
 0.026792 
 NaN 
 NaN 
 1.914692 
 ... 
 1.182542e+06 
 72.519229 
 6.935152 
 0.665117 
 0.768344 
 0.497995 
 0.579425 
 0.719816 
 0.796915 
 313.282220 
 
 
 min 
 NaN 
 NaN 
 NaN 
 0.000000 
 NaN 
 37.707430 
 -122.513060 
 NaN 
 NaN 
 1.000000 
 ... 
 1.000000e+00 
 0.000000 
 20.000000 
 2.000000 
 2.000000 
 2.000000 
 2.000000 
 2.000000 
 2.000000 
 0.000000 
 
 
 25% 
 NaN 
 NaN 
 NaN 
 1.000000 
 NaN 
 37.751125 
 -122.442950 
 NaN 
 NaN 
 2.000000 
 ... 
 2.000000e+00 
 1.000000 
 94.000000 
 10.000000 
 9.000000 
 10.000000 
 10.000000 
 9.000000 
 9.000000 
 100.000000 
 
 
 50% 
 NaN 
 NaN 
 NaN 
 2.000000 
 NaN 
 37.767550 
 -122.425470 
 NaN 
 NaN 
 2.000000 
 ... 
 4.000000e+00 
 11.000000 
 98.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 150.000000 
 
 
 75% 
 NaN 
 NaN 
 NaN 
 8.000000 
 NaN 
 37.784615 
 -122.411070 
 NaN 
 NaN 
 4.000000 
 ... 
 3.000000e+01 
 54.000000 
 100.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 235.000000 
 
 
 max 
 NaN 
 NaN 
 NaN 
 1199.000000 
 NaN 
 37.810310 
 -122.369790 
 NaN 
 NaN 
 16.000000 
 ... 
 1.000000e+08 
 677.000000 
 100.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10.000000 
 10000.000000 
 
 
 
 11 rows × 24 columns

### Getting rid of extreme values in column 'price'

In [0]:
print(fixedPriceDF["price"].describe())

count     7151.000000
mean       213.654034
std        313.282220
min          0.000000
25%        100.000000
50%        150.000000
75%        235.000000
max      10000.000000
Name: price, dtype: float64


#Filter the "free" Airbnbs.

In [0]:
fixedPriceDF['price'].loc[fixedPriceDF["price"] == 0].count()

Out[12]: 1

Now only keep rows with a strictly positive *price*.

In [0]:
posPricesDF = fixedPriceDF.loc[fixedPriceDF["price"] > 0]
posPricesDF.count()

Out[13]: host_is_superhost              7150
cancellation_policy            7150
instant_bookable               7150
host_total_listings_count      7150
neighbourhood_cleansed         7150
latitude                       7150
longitude                      7150
property_type                  7150
room_type                      7150
accommodates                   7150
bathrooms                      7129
bedrooms                       7148
beds                           7143
bed_type                       7150
minimum_nights                 7150
number_of_reviews              7150
review_scores_rating           5729
review_scores_accuracy         5725
review_scores_cleanliness      5726
review_scores_checkin          5723
review_scores_communication    5727
review_scores_location         5723
review_scores_value            5722
price                          7150
dtype: int64

Look at the *min* and *max* values of the *minimum_nights* column:

In [0]:
posPricesDF[["minimum_nights"]].describe()

minimum_nights 
 
 
 
 
 count 
 7.150000e+03 
 
 
 mean 
 1.400226e+04 
 
 
 std 
 1.182625e+06 
 
 
 min 
 1.000000e+00 
 
 
 25% 
 2.000000e+00 
 
 
 50% 
 4.000000e+00 
 
 
 75% 
 3.000000e+01 
 
 
 max 
 1.000000e+08

In [0]:
(posPricesDF[["minimum_nights",'price']].groupby("minimum_nights",as_index=False)
.count()
.rename(columns={'price':'count'})
.sort_values(["count","minimum_nights"],ascending=False))

minimum_nights 
 count 
 
 
 
 
 19 
 30 
 2757 
 
 
 1 
 2 
 1455 
 
 
 0 
 1 
 1251 
 
 
 2 
 3 
 822 
 
 
 3 
 4 
 270 
 
 
 4 
 5 
 176 
 
 
 20 
 31 
 133 
 
 
 6 
 7 
 72 
 
 
 28 
 60 
 32 
 
 
 21 
 32 
 31 
 
 
 5 
 6 
 31 
 
 
 38 
 180 
 28 
 
 
 33 
 90 
 28 
 
 
 44 
 365 
 7 
 
 
 24 
 45 
 7 
 
 
 35 
 120 
 6 
 
 
 11 
 14 
 4 
 
 
 23 
 40 
 3 
 
 
 9 
 10 
 3 
 
 
 39 
 183 
 2 
 
 
 31 
 80 
 2 
 
 
 25 
 50 
 2 
 
 
 17 
 28 
 2 
 
 
 48 
 100000000 
 1 
 
 
 47 
 1125 
 1 
 
 
 46 
 1000 
 1 
 
 
 45 
 999 
 1 
 
 
 43 
 360 
 1 
 
 
 42 
 270 
 1 
 
 
 41 
 200 
 1 
 
 
 40 
 188 
 1 
 
 
 37 
 170 
 1 
 
 
 36 
 140 
 1 
 
 
 34 
 100 
 1 
 
 
 32 
 85 
 1 
 
 
 30 
 75 
 1 
 
 
 29 
 70 
 1 
 
 
 27 
 59 
 1 
 
 
 26 
 58 
 1 
 
 
 22 
 35 
 1 
 
 
 18 
 29 
 1 
 
 
 16 
 25 
 1 
 
 
 15 
 24 
 1 
 
 
 14 
 21 
 1 
 
 
 13 
 18 
 1 
 
 
 12 
 17 
 1 
 
 
 10 
 13 
 1 
 
 
 8 
 9 
 1 
 
 
 7 
 8 
 1

Filter out those records where the *minimum_nights* is greater then 365:

In [0]:
minNightsDF = posPricesDF[posPricesDF["minimum_nights"]<= 365]

minNightsDF[["minimum_nights"]].describe()

minimum_nights 
 
 
 
 
 count 
 7146.000000 
 
 
 mean 
 15.817800 
 
 
 std 
 22.511624 
 
 
 min 
 1.000000 
 
 
 25% 
 2.000000 
 
 
 50% 
 4.000000 
 
 
 75% 
 30.000000 
 
 
 max 
 365.000000

### Nulls

There are a lot of different ways to handle null values. Sometimes, null can actually be a key indicator of the thing you are trying to predict (e.g. if you don't fill in certain portions of a form, probability of it getting approved decreases).

Some ways to handle nulls:
* Drop any records that contain nulls
* Numeric:
  * Replace them with mean/median/zero/etc.
* Categorical:
  * Replace them with the mode
  * Create a special category for null
* Use techniques like ALS which are designed to impute missing values

Select columns which have Nan values

In [0]:
#7150 is the max number of rows
columns_na=minNightsDF.loc[:,minNightsDF.isna().any()].columns.tolist()
columns_na

Out[17]: ['bathrooms',
 'bedrooms',
 'beds',
 'review_scores_rating',
 'review_scores_accuracy',
 'review_scores_cleanliness',
 'review_scores_checkin',
 'review_scores_communication',
 'review_scores_location',
 'review_scores_value']

In [0]:
#isna return true or false and sum convert to 0 & 1
minNightsDF.isna().sum()

Out[18]: host_is_superhost                 0
cancellation_policy               0
instant_bookable                  0
host_total_listings_count         0
neighbourhood_cleansed            0
latitude                          0
longitude                         0
property_type                     0
room_type                         0
accommodates                      0
bathrooms                        21
bedrooms                          2
beds                              7
bed_type                          0
minimum_nights                    0
number_of_reviews                 0
review_scores_rating           1421
review_scores_accuracy         1425
review_scores_cleanliness      1424
review_scores_checkin          1427
review_scores_communication    1423
review_scores_location         1427
review_scores_value            1428
price                             0
dtype: int64

Create a new column for each one which has NaN values and substitute the respective row with 1, otherwise set 0

In [0]:
import numpy as np
for x in columns_na:
  minNightsDF[x+'_na']=np.where(minNightsDF[x].isna(),1,0)
#show some row and cols with null values
display(minNightsDF[['bathrooms','bathrooms_na','bedrooms','bedrooms_na']]
       .loc[minNightsDF[['bathrooms','bathrooms_na','bedrooms','bedrooms_na']].isna().any(axis=1),:])

<command-3769254019830727>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  minNightsDF[x+'_na']=np.where(minNightsDF[x].isna(),1,0)


bathrooms bathrooms_na bedrooms bedrooms_na null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 1.0 0 null 1 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 null 1 1.0 0 3.5 0 null 1

### Transformers and Estimators

Every col should have 7146 rows

In [0]:
minNightsDF.count()

Out[20]: host_is_superhost                 7146
cancellation_policy               7146
instant_bookable                  7146
host_total_listings_count         7146
neighbourhood_cleansed            7146
latitude                          7146
longitude                         7146
property_type                     7146
room_type                         7146
accommodates                      7146
bathrooms                         7125
bedrooms                          7144
beds                              7139
bed_type                          7146
minimum_nights                    7146
number_of_reviews                 7146
review_scores_rating              5725
review_scores_accuracy            5721
review_scores_cleanliness         5722
review_scores_checkin             5719
review_scores_communication       5723
review_scores_location            5719
review_scores_value               5718
price                             7146
bathrooms_na                      7146
bedrooms_na     

In [0]:
from sklearn.impute import SimpleImputer
#replace every nan value with the actual median of the column(only numeric cols)
Imputer=SimpleImputer(strategy='median')
numeric_cols=minNightsDF.select_dtypes(exclude='object').columns.tolist()
minNightsDF[numeric_cols]=Imputer.fit_transform(minNightsDF[numeric_cols])
minNightsDF.count()

<command-1540239115776695>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  minNightsDF[numeric_cols]=Imputer.fit_transform(minNightsDF[numeric_cols])
/databricks/python/lib/python3.8/site-packages/pandas/core/indexing.py:1738: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value[:, i].tolist(), pi)
Out[21]: host_is_superhost                 7146
cancellation_policy               7146
instant_bookable                  7146
host_total_listings_count         7146
neighbourhood_

In [0]:
display(minNightsDF[numeric_cols].loc[minNightsDF[[
 'bathrooms_na',
 'bedrooms_na',
 'beds_na',
 'review_scores_rating_na',
 'review_scores_accuracy_na',
 'review_scores_cleanliness_na',
 'review_scores_checkin_na',
 'review_scores_communication_na',
 'review_scores_location_na',
 'review_scores_value_na']].any(axis=1)==1,:])

host_total_listings_count latitude longitude accommodates bathrooms bedrooms beds minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price bathrooms_na bedrooms_na beds_na review_scores_rating_na review_scores_accuracy_na review_scores_cleanliness_na review_scores_checkin_na review_scores_communication_na review_scores_location_na review_scores_value_na 2.0 37.75121 -122.42165 4.0 1.0 1.0 2.0 31.0 3.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 175.0 0.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 37.79667 -122.41272 1.0 1.0 1.0 1.0 30.0 166.0 89.0 9.0 9.0 9.0 9.0 9.0 9.0 99.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 9.0 37.79216 -122.42458 1.0 1.0 1.0 1.0 30.0 120.0 92.0 9.0 8.0 10.0 10.0 10.0 9.0 55.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 37.75674 -122.49178 2.0 1.0 1.0 1.0 60.0 1.0 20.0 10.0 10.0 10.0 2.0 10.0 10.0 100.0 0.0 0.0 0.0 0.0 1.0 1.0 1.0 0.0 1.0 1.0 20.0 37.79447 -122.4045 1.0 1.0 1.0 1.0 1.0 356.0 92.0 10.0 10.0 10.0 10.0 10.0 10.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.79309 -122.40443 2.0 1.0 1.0 2.0 1.0 352.0 94.0 10.0 9.0 10.0 10.0 10.0 9.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 9.0 37.79176 -122.42476 1.0 1.0 1.0 1.0 30.0 130.0 94.0 10.0 9.0 10.0 10.0 10.0 9.0 59.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 9.0 37.79336 -122.42506 1.0 1.0 1.0 1.0 30.0 117.0 93.0 10.0 9.0 10.0 10.0 10.0 9.0 56.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 37.77579 -122.50702 2.0 1.0 1.0 1.0 30.0 0.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 162.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 20.0 37.79341 -122.4034 3.0 1.0 1.0 3.0 1.0 319.0 93.0 10.0 9.0 10.0 10.0 10.0 9.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.7947 -122.40374 1.0 1.0 1.0 1.0 1.0 199.0 92.0 10.0 9.0 10.0 9.0 10.0 9.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.79441 -122.40473 5.0 1.0 1.0 5.0 1.0 196.0 94.0 10.0 9.0 10.0 10.0 10.0 10.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 37.79586 -122.43035 1.0 1.0 1.0 1.0 30.0 1.0 80.0 10.0 10.0 10.0 10.0 10.0 10.0 160.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 37.72606 -122.43232 1.0 1.0 1.0 1.0 2.0 60.0 98.0 10.0 9.0 10.0 10.0 9.0 10.0 48.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 37.72636 -122.43342 2.0 1.0 1.0 1.0 30.0 0.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 85.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 37.79178 -122.39502 4.0 2.0 2.0 2.0 30.0 1.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 500.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 6.0 37.75906 -122.40761 1.0 1.0 1.0 1.0 31.0 12.0 98.0 10.0 9.0 10.0 10.0 10.0 10.0 80.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 41.0 37.78321 -122.41969 2.0 1.0 1.0 1.0 30.0 8.0 95.0 9.0 10.0 10.0 9.0 9.0 8.0 124.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 7.0 37.79478 -122.40592 1.0 2.5 1.0 1.0 30.0 6.0 97.0 10.0 8.0 10.0 10.0 10.0 9.0 30.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.79472 -122.40519 1.0 2.5 1.0 1.0 30.0 1.0 100.0 8.0 6.0 8.0 8.0 10.0 10.0 30.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 9.0 37.79384 -122.42436 1.0 1.0 1.0 1.0 30.0 95.0 96.0 10.0 9.0 10.0 10.0 10.0 9.0 63.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 37.78307 -122.46075 2.0 1.0 1.0 2.0 2.0 6.0 93.0 9.0 9.0 9.0 10.0 9.0 9.0 150.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 37.77532 -122.43741 1.0 1.5 1.0 1.0 30.0 0.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 67.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 2.0 37.79139 -122.44552 5.0 2.5 2.0 2.0 30.0 0.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 240.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 20.0 37.79313 -122.40443 2.0 1.0 1.0 2.0 1.0 176.0 93.0 9.0 9.0 10.0 10.0 10.0 9.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.79421 -122.4031 3.0 1.0 1.0 3.0 1.0 172.0 94.0 10.0 9.0 10.0 10.0 10.0 10.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 20.0 37.7926 -122.40339 4.0 1.0 1.0 1.0 1.0 174.0 94.0 9.0 9.0 10.0 10.0 10.0 9.0 45.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 5.0 37.79119 -122.39564 4.0 2.0 2

In [0]:
minNightsDF.describe()

host_total_listings_count 
 latitude 
 longitude 
 accommodates 
 bathrooms 
 bedrooms 
 beds 
 minimum_nights 
 number_of_reviews 
 review_scores_rating 
 ... 
 bathrooms_na 
 bedrooms_na 
 beds_na 
 review_scores_rating_na 
 review_scores_accuracy_na 
 review_scores_cleanliness_na 
 review_scores_checkin_na 
 review_scores_communication_na 
 review_scores_location_na 
 review_scores_value_na 
 
 
 
 
 count 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 ... 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 7146.000000 
 
 
 mean 
 52.604954 
 37.765812 
 -122.430534 
 3.201092 
 1.328086 
 1.342709 
 1.764484 
 15.817800 
 43.553876 
 96.034285 
 ... 
 0.002939 
 0.000280 
 0.000980 
 0.198853 
 0.199412 
 0.199272 
 0.199692 
 0.199132 
 0.199692 
 0.199832 
 
 
 std 
 177.428653 
 0.022531 
 0.026799 
 1.914916 
 0.793787 
 0.932855 
 1.176789 
 22.511624 
 72.538481 
 6.286139 
 ... 
 0.054134 
 0.016728 
 0.031285 
 0.399165 
 0.399586 
 0.399481 
 0.399797 
 0.399376 
 0.399797 
 0.399902 
 
 
 min 
 0.000000 
 37.707430 
 -122.513060 
 1.000000 
 0.000000 
 0.000000 
 0.000000 
 1.000000 
 0.000000 
 20.000000 
 ... 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 
 
 25% 
 1.000000 
 37.751140 
 -122.442972 
 2.000000 
 1.000000 
 1.000000 
 1.000000 
 2.000000 
 1.000000 
 95.000000 
 ... 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 
 
 50% 
 2.000000 
 37.767570 
 -122.425490 
 2.000000 
 1.000000 
 1.000000 
 1.000000 
 4.000000 
 11.000000 
 98.000000 
 ... 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 
 
 75% 
 8.000000 
 37.784617 
 -122.411070 
 4.000000 
 1.500000 
 2.000000 
 2.000000 
 30.000000 
 54.000000 
 99.000000 
 ... 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 0.000000 
 
 
 max 
 1199.000000 
 37.810310 
 -122.369790 
 16.000000 
 14.000000 
 14.000000 
 14.000000 
 365.000000 
 677.000000 
 100.000000 
 ... 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 1.000000 
 
 
 
 8 rows × 27 columns

I will save this DataFrame to Delta so that I can start building models with it.

In [0]:
outputPath = userhome + "/machine-learning-p/airbnb-cleansed.delta"

spark.createDataFrame(minNightsDF).write.format("delta").mode("overwrite").save(outputPath)

## Build a linear regression model to estimate the price of airbnb houses
 - Encode categorical features
 - Build a Linear regression Model
 - Calculate RMSE,MSE,MAE

In [0]:
airbnbDF=spark.read.format('delta').load(outputPath).toPandas()

In [0]:
df=airbnbDF.copy()

In [0]:
cols_numeric=[
'host_total_listings_count',
'latitude',
'longitude',
'accommodates',
'bathrooms',
'bedrooms',
'beds',
'minimum_nights',
'number_of_reviews',
'review_scores_rating',
'review_scores_accuracy',
'review_scores_cleanliness',
'review_scores_checkin',
'review_scores_communication',
'review_scores_location',
'review_scores_value']
cols_categorical=df.select_dtypes(include='object').columns.tolist()

# What Are the Basic Assumption?(favourite)
There are four assumptions associated with a linear regression model:

- Linearity: The relationship between X and the mean of Y is linear.
- Homoscedasticity: The variance of residual is the same for any value of X.
- Independence: Observations are independent of each other.
- Normality: For any fixed value of X, Y is normally distributed.

In [0]:
#standirzed the numerical columns
from sklearn.preprocessing import StandardScaler
SC=StandardScaler()
df[cols_numeric]=SC.fit_transform(df[cols_numeric])
display(df)

host_is_superhost cancellation_policy instant_bookable host_total_listings_count neighbourhood_cleansed latitude longitude property_type room_type accommodates bathrooms bedrooms beds bed_type minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price bedrooms_na bathrooms_na beds_na review_scores_rating_na review_scores_accuracy_na review_scores_cleanliness_na review_scores_checkin_na review_scores_communication_na review_scores_location_na review_scores_value_na f moderate f -0.2795964703034248 Noe Valley -0.6689989750513833 -0.17152674551003233 Apartment Entire home/apt 0.41723201998248577 -0.4133456954166042 0.7046508700644518 0.20014876728301847 Real Bed 0.6300385948331374 -0.5591061977741674 0.6309106909062873 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.6328924548612103 170.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f strict_14_with_grace_period f -0.28523293297036306 Noe Valley -0.890047462145707 0.15052756519753907 House Entire home/apt 1.4617371924452092 3.3662683025962603 2.848757796817942 1.8998078177933577 Real Bed -0.39172727031777926 -0.5728929488535198 0.6309106909062873 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 -1.090922378073247 -3.358854661147803 710.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f strict_14_with_grace_period f -0.2908693956373013 Noe Valley -0.5584747315042213 -0.19951524296421994 House Entire home/apt 1.9839897786765708 2.1063969699253056 2.848757796817942 1.8998078177933577 Real Bed -0.48057647598307635 -0.47638569129805225 0.6309106909062873 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.6328924548612103 1100.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t flexible f -0.28523293297036306 Noe Valley -0.8691854563356154 -0.248401818517902 Apartment Entire home/apt -0.6272731524802375 -0.4133456954166042 -0.3674025933122933 -0.6496807579721512 Real Bed 0.6300385948331374 -0.46259894021869974 0.6309106909062873 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.6328924548612103 160.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t moderate t -0.2683235449695483 Downtown/Civic Center 0.950247773782952 0.7826944276992911 Serviced apartment Entire home/apt 0.41723201998248577 -0.4133456954166042 -0.3674025933122933 0.20014876728301847 Real Bed -0.613850284481022 -0.228224171869707 0.3127281299679111 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.6328924548612103 195.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t strict_14_with_grace_period f -0.28523293297036306 Potrero Hill -0.15011206458325801 1.0704161815298034 House Private room 0.9394846062138474 -0.4133456954166042 -0.3674025933122933 1.0499782925381882 Real Bed 0.6300385948331374 -0.49017244237740476 0.6309106909062873 -1.3627744688461338 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.6328924548612103 150.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t strict_14_with_grace_period f -0.27396000763648654 Noe Valley -0.6090761924052746 0.16732066367015772 House Entire home/apt 1.4617371924452092 0.8465256372543507 2.848757796817942 1.8998078177933577 Real Bed -0.5250010788157249 -0.32473142942517463 0.3127281299679111 -1.3627744688461338 -0.9939253518444698 0.23204948179892843 0.24342343936120228 0.4260519970408653 -0.6976899171417943 399.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f moderate f -0.2908693956373013 Castro/Upper Market -0.10794418049920466 -0.24056503923085673 Apartment Entire home/apt -0.6272731524802375 -0.4133456954166042 -0.3674025933122933 -0.6496807579721512 Real Bed 0.6300385948331374 -0.5177459445361098 0.6309106909062873 0.2984992183552441 0.42687692146630757 0.23204948179892843 0.24342343936120228 0.4260519970408653 0.632892

In [0]:
#Compare original dataframe with the copy of that
print(len(df.loc[:,df.columns!='price'].select_dtypes(exclude='object').columns.tolist()),len(
      airbnbDF.loc[:,airbnbDF.columns!='price'].select_dtypes(exclude='object').columns.tolist()))

26 26


In [0]:
cols_categorical=df.select_dtypes(include='object').columns.tolist()
print(len(df.select_dtypes(include='object').columns.tolist()),len(airbnbDF.select_dtypes(include='object').columns.tolist()))

7 7


In [0]:
#Use OHE in categorical features
import pandas as pd
df=pd.get_dummies(df,drop_first=True,columns=cols_categorical)
df.head(15)

host_total_listings_count 
 latitude 
 longitude 
 accommodates 
 bathrooms 
 bedrooms 
 beds 
 minimum_nights 
 number_of_reviews 
 review_scores_rating 
 ... 
 property_type_Tiny house 
 property_type_Townhouse 
 property_type_Treehouse 
 property_type_Villa 
 room_type_Private room 
 room_type_Shared room 
 bed_type_Couch 
 bed_type_Futon 
 bed_type_Pull-out Sofa 
 bed_type_Real Bed 
 
 
 
 
 0 
 -0.279596 
 -0.668999 
 -0.171527 
 0.417232 
 -0.413346 
 0.704651 
 0.200149 
 0.630039 
 -0.559106 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 1 
 -0.285233 
 -0.890047 
 0.150528 
 1.461737 
 3.366268 
 2.848758 
 1.899808 
 -0.391727 
 -0.572893 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 2 
 -0.290869 
 -0.558475 
 -0.199515 
 1.983990 
 2.106397 
 2.848758 
 1.899808 
 -0.480576 
 -0.476386 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 3 
 -0.285233 
 -0.869185 
 -0.248402 
 -0.627273 
 -0.413346 
 -0.367403 
 -0.649681 
 0.630039 
 -0.462599 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 4 
 -0.268324 
 0.950248 
 0.782694 
 0.417232 
 -0.413346 
 -0.367403 
 0.200149 
 -0.613850 
 -0.228224 
 0.312728 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 5 
 -0.285233 
 -0.150112 
 1.070416 
 0.939485 
 -0.413346 
 -0.367403 
 1.049978 
 0.630039 
 -0.490172 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 
 
 6 
 -0.273960 
 -0.609076 
 0.167321 
 1.461737 
 0.846526 
 2.848758 
 1.899808 
 -0.525001 
 -0.324731 
 0.312728 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 7 
 -0.290869 
 -0.107944 
 -0.240565 
 -0.627273 
 -0.413346 
 -0.367403 
 -0.649681 
 0.630039 
 -0.517746 
 0.630911 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 8 
 -0.290869 
 -0.460379 
 -0.175632 
 0.417232 
 -0.413346 
 0.704651 
 0.200149 
 -0.569426 
 0.226739 
 0.312728 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 9 
 0.272777 
 1.313335 
 0.063950 
 -0.627273 
 -0.413346 
 -0.367403 
 -0.649681 
 0.630039 
 -0.572893 
 -5.732741 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 10 
 -0.290869 
 -0.040476 
 0.340849 
 -1.149526 
 -0.413346 
 -0.367403 
 -0.649681 
 -0.613850 
 0.268099 
 0.312728 
 ... 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 
 
 11 
 -0.290869 
 -0.436410 
 0.570355 
 -0.627273 
 -0.413346 
 -0.367403 
 -0.649681 
 -0.658275 
 0.502474 
 0.312728 
 ... 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 
 
 12 
 -0.290869 
 -0.551817 
 0.903232 
 2.506242 
 0.216590 
 1.776704 
 2.749637 
 -0.569426 
 -0.048996 
 0.153637 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 13 
 -0.290869 
 0.863693 
 0.273304 
 -0.627273 
 -0.413346 
 -0.367403 
 -0.649681 
 -0.569426 
 -0.269584 
 0.153637 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 14 
 -0.290869 
 -0.561582 
 0.948760 
 0.939485 
 -0.413346 
 0.704651 
 1.049978 
 -0.569426 
 -0.462599 
 -0.641820 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 
 
 
 15 rows × 100 columns

In [0]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error,mean_absolute_error,r2_score

X=df.loc[:,df.columns!='price']
y=df['price']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
#Build the model
lr=LinearRegression()
lr.fit(X_train,y_train)
#Evaluate the model
y_pred=lr.predict(X_test)

print('The mse error is:',mean_squared_error(y_test,y_pred))
print('The rmse error is:',np.sqrt(mean_squared_error(y_test,y_pred)))
print('The mae error is:',mean_absolute_error(y_test,y_pred))
print('The value of R2 is:',r2_score(y_test,y_pred))

The mse error is: 40855.33974276679
The rmse error is: 202.12703862365072
The mae error is: 89.57785436460726
The value of R2 is: 0.2656381583289351


1. I will use the Lasso(L1) regression to compare values

In [0]:
from sklearn.linear_model import Lasso
#Build the model
la=Lasso(alpha=1)
la.fit(X_train,y_train)
#Evaluate the model
y_la_pred=lr.predict(X_test)
print('The mse error is:',mean_squared_error(y_test,y_la_pred))
print('The rmse error is:',np.sqrt(mean_squared_error(y_test,y_la_pred)))
print('The mae error is:',mean_absolute_error(y_test,y_la_pred))
print('The value of R2 is:',r2_score(y_test,y_la_pred))

The mse error is: 40855.33974276679
The rmse error is: 202.12703862365072
The mae error is: 89.57785436460726
The value of R2 is: 0.2656381583289351


1. I will use the Ridge(L2) regression to compare values

In [0]:
from sklearn.linear_model import Ridge
#Build the model
rd=Ridge(alpha=1)
rd.fit(X_train,y_train)
#Evaluate the model
y_rd_pred=rd.predict(X_test)
print('The mse error is:',mean_squared_error(y_test,y_rd_pred))
print('The rmse error is:',np.sqrt(mean_squared_error(y_test,y_rd_pred)))
print('The mae error is:',mean_absolute_error(y_test,y_rd_pred))
print('The value of R2 is:',r2_score(y_test,y_rd_pred))

The mse error is: 40842.30792952824
The rmse error is: 202.09479936289364
The mae error is: 89.48749837757455
The value of R2 is: 0.2658724010602508
